In [3]:
from datasets import load_dataset
import pandas as pd 
from pymongo import MongoClient
from transformers import BertTokenizer, BertForMaskedLM, DPRContextEncoderTokenizer,DPRContextEncoder;
from sklearn.feature_extraction.text import TfidfVectorizer
import numpy as np
import re
import pandas as pd
from nltk.stem import WordNetLemmatizer
from nltk.corpus import stopwords as nltk_stopwords
from transformers import BertTokenizer, BertModel, AutoTokenizer
from sklearn.metrics.pairwise import cosine_similarity
import torch
from pymongo import MongoClient
import torch.nn.functional as F

In [8]:
import pandas as pd
import re
from nltk.corpus import stopwords
from transformers import AutoTokenizer

#------------------------cümlelerin boyutlarını ve stop wordsleri tanımladığımız yer -----------------------------
import spacy
from spacy.lang.tr import Turkish

nlp = Turkish()

def truncate_text_meaningful(text, max_len=300):
    doc = nlp(text)

    # Stop kelimeleri ve noktalama işaretlerini kaldır
    tokens = [token.lemma_ for token in doc if not token.is_stop and not token.is_punct]

    # Named Entity Recognition (isteğe bağlı)
    # for ent in doc.ents:
    #     print(ent.text, ent.label_)

    # Belirli bir uzunluktaki metni döndür
    truncated_text = ' '.join(tokens[:max_len])

    return truncated_text
        

    

  

#----------------------------------tokenize etme fonksiyonu-----------------------------------
def tokenize_and_pad(data, model_name='bert-base-uncased', max_length=512):
    tokenizer = AutoTokenizer.from_pretrained(model_name)
    encoded_input = tokenizer(data, padding=True, truncation=True, max_length=max_length)
    return encoded_input

class DataProcessor:
    def __init__(self, input_csv, output_csv, max_words=300, model_name='dbmdz/distilbert-base-turkish-cased'):
        self.input_csv = input_csv
        self.output_csv = output_csv
        self.max_words = max_words
        self.model_name = model_name

    def main_pipeline(self):

        def filter_text(text):
            # Dış bağlantılar ve kaynakçaları kaldır
            text = re.sub(r'http\S+|https\S+|\b(?:www\.)?\S+\.\w{2,4}\b', '', text)
            # Tarih ve sayıları kaldır
            text = re.sub(r'\d{4}-\d{2}-\d{2}|\d{2}/\d{2}/\d{4}|\d+', '', text)  # Tari
            # Sayıları kaldır
            text = re.sub(r'\d+', '', text)
            # Kısa veya uzun kelimeleri kaldır
            words = text.split()
            words = [word for word in words if 2 <= len(word) <= 20]
            return ' '.join(words)
        
        df = pd.read_csv(self.input_csv)
        df['kısaltılmıs_metin'] = df['metinler'].apply(filter_text)

        

        # Metinleri kısalt
        df['kısaltılmıs_metin'] = df['metinler'].apply(lambda x: truncate_text_meaningful(x, max_len=self.max_words))
        padded_tokens = tokenize_and_pad(df['kısaltılmıs_metin'].tolist(), model_name=self.model_name)
        df['padded_tokens'] = padded_tokens['input_ids']
        print("Kısaltılmış metinler:")
        print(df['kısaltılmıs_metin'].head())
        print("Tokenize edilmiş ve padding uygulanmış veriler:")
        print(df[['kısaltılmıs_metin', 'padded_tokens']].head())
        
        

        # Veriyi kaydet
        self.save_cleaned_data(df)
    
        return self.output_csv
        

    def save_cleaned_data(self, df):
        df.to_csv(self.output_csv, index=False)
        print(f"Temizlenmiş veri '{self.output_csv}' dosyasına kaydedildi.")

#---------------------------------Verilerin kaydedilmesi-------------------------------------

processor = DataProcessor(input_csv="texts_egitim.csv", output_csv="cleaned_data3.csv")
processor.main_pipeline()


Kısaltılmış metinler:
0    Alman tarihçileri Alman sosyologlar Alman devr...
1    Diskografi : Seferberlik Türküleri Kuvayi Mill...
2    Modern bilgisayarlar Ayrıca Bilgisayarlar Bilg...
3                             Ayrıca Kaynakça Edebiyat
4    Ayrıca Mühendislik Mühendislik dalları Mühendi...
Name: kısaltılmıs_metin, dtype: object
Tokenize edilmiş ve padding uygulanmış veriler:
                                   kısaltılmıs_metin  \
0  Alman tarihçileri Alman sosyologlar Alman devr...   
1  Diskografi : Seferberlik Türküleri Kuvayi Mill...   
2  Modern bilgisayarlar Ayrıca Bilgisayarlar Bilg...   
3                           Ayrıca Kaynakça Edebiyat   
4  Ayrıca Mühendislik Mühendislik dalları Mühendi...   

                                       padded_tokens  
0  [2, 3651, 2465, 10576, 3651, 23906, 7131, 1980...  
1  [2, 28488, 12922, 30, 17749, 3251, 2102, 22548...  
2  [2, 11368, 26726, 3401, 7682, 1980, 7682, 7682...  
3  [2, 3401, 7934, 2548, 8558, 3, 0, 0, 0, 0, 0, ...  
4  [

'cleaned_data3.csv'

In [9]:
import pandas as pd

# CSV dosyasını oku
df = pd.read_csv('cleaned_data3.csv')

# Görmek istediğiniz üç sütunu seçin
selected_columns = df[['kısaltılmıs_metin']]

# Seçilen sütunları tablo olarak görüntüle
print(selected_columns)

# Eğer Jupyter Notebook kullanıyorsanız, daha güzel görüntü için display() fonksiyonunu kullanabilirsiniz:
from IPython.display import display
display(selected_columns)


                                        kısaltılmıs_metin
0       Alman tarihçileri Alman sosyologlar Alman devr...
1       Diskografi : Seferberlik Türküleri Kuvayi Mill...
2       Modern bilgisayarlar Ayrıca Bilgisayarlar Bilg...
3                                Ayrıca Kaynakça Edebiyat
4       Ayrıca Mühendislik Mühendislik dalları Mühendi...
...                                                   ...
104103               Dış bağlantılar Kaynakça Cicerininae
104104               Dış bağlantılar Kaynakça Cicerininae
104105                                   Lig futbolcuları
104106           Dış bağlantılar Kaynakça Kalyptorhynchia
104107  Dış bağlantılar 'de Japonya'da oluşumlar 'de b...

[104108 rows x 1 columns]


kısaltılmıs_metin
0       Alman tarihçileri Alman sosyologlar Alman devr...
1       Diskografi : Seferberlik Türküleri Kuvayi Mill...
2       Modern bilgisayarlar Ayrıca Bilgisayarlar Bilg...
3                                Ayrıca Kaynakça Edebiyat
4       Ayrıca Mühendislik Mühendislik dalları Mühendi...
...                                                   ...
104103               Dış bağlantılar Kaynakça Cicerininae
104104               Dış bağlantılar Kaynakça Cicerininae
104105                                   Lig futbolcuları
104106           Dış bağlantılar Kaynakça Kalyptorhynchia
104107  Dış bağlantılar 'de Japonya'da oluşumlar 'de b...

[104108 rows x 1 columns]

In [10]:
from gensim import corpora
from gensim.models import LdaMulticore
import pandas as pd

# CSV dosyasını okuma
df = pd.read_csv('cleaned_data3.csv')

# Verinin bir alt kümesini seçme
df_sample = df.sample(n=10000, random_state=100)

# Kelimeleri token'lara ayırma
tokenized_text = [text.split() for text in df_sample['kısaltılmıs_metin']]

# Dictionary ve Corpus oluşturma
id2word = corpora.Dictionary(tokenized_text)
corpus = [id2word.doc2bow(text) for text in tokenized_text]

# LDA Modelini Eğitme
lda_model = LdaMulticore(
    corpus=corpus,
    id2word=id2word,
    num_topics=5,
    random_state=100,
    chunksize=50,
    passes=5,
    alpha='symmetric',
    eta='auto',
    per_word_topics=True,
    workers=4  # Paralel iş parçacıkları kullanarak performansı artırır
)

# Sonuçları görüntüleme
for idx, topic in lda_model.print_topics(-1):
    print(f"Topic: {idx}\nWords: {topic}\n")

# Alt kümesini kaydetme
df_sample.to_csv('cleaned_processed_data_sample.csv', index=False)


AttributeError: 'float' object has no attribute 'split'